In [1]:
import pandas as pd
import numpy as np


In [2]:
f = pd.DataFrame.from_csv('apartments.csv')

In [3]:
f.head()

Latitude  Longitude  Bedrooms  Bathrooms  Square footage  Price  \
Id                                                                     
1   42.325319 -71.142400         2          1            1162   2722   
2   42.400188 -71.123543         0          1             260    948   
3   42.390901 -71.152410         3          3            2016   3418   
4   42.351352 -71.109718         2          1            1163   2583   
5   42.383498 -71.130352         2          2            1006   2800   

                                            Amenities  
Id                                                     
1   Secure Entrance|Central Air|Picnic Area|Pool|W...  
2                          Central Air|Fitness Center  
3         Washer/Dryer|Central Air|Utilities Included  
4   Granite Countertops|Utilities Included|Stainle...  
5                    Granite Countertops|Washer/Dryer

In [19]:

f['locations'] = f.apply(lambda x: [x['Latitude'], x['Longitude']], axis=1) 
f.head()

Latitude  Longitude  Bedrooms  Bathrooms  Square footage  Price  \
Id                                                                     
1   42.325319 -71.142400         2          1            1162   2722   
2   42.400188 -71.123543         0          1             260    948   
3   42.390901 -71.152410         3          3            2016   3418   
4   42.351352 -71.109718         2          1            1163   2583   
5   42.383498 -71.130352         2          2            1006   2800   

                                            Amenities                locations  
Id                                                                              
1   Secure Entrance|Central Air|Picnic Area|Pool|W...    [42.325319, -71.1424]  
2                          Central Air|Fitness Center  [42.400188, -71.123543]  
3         Washer/Dryer|Central Air|Utilities Included   [42.390901, -71.15241]  
4   Granite Countertops|Utilities Included|Stainle...  [42.351352, -71.109718]  
5                    Granite Countertops|Washer/Dryer  [42.383498, -71.130352]

# Data/Analytics engineer programming exercise

- Use the programming language of your choice to answer the following questions. Please ensure your code can be run on a modern machine and briefly explain why you chose that language.

- - Based on the apartments in apartments.csv:

- Which two apartments are closest to each other? Which two are farthest from each other? 
- - Please include the apartment ids and each of the distances in miles rounded to two decimal places.

- Find the min and max rents. 
- - Choose a random integer in that range (inclusive), then find the number of apartments at that price or less that have Granite Countertops.

- A friend wants an apartment with Central Air and at least three other amenities. Which apartment fulfilling these criteria has the best price per square foot and what is it, rounded to the nearest cent?

- Another friend also wants to investigate the apartment options and finds more listings for you to consider. Make a GET request to http://52.201.94.104:8080 with query params first_id=1001 and last_id=1050. You'll get a JSON response looking like:

[
{
"Bathrooms": 1,
"Price": 751,
"Bedrooms": 0,
"Longitude": -71.14077475024915,
"Amenities": [
"Granite Countertops",
"Dishwasher"
],
"Square footage": 863,
"Latitude": 42.11827987606943,
"Id": 1001
},
...
]

# Problem 1
- Which two apartments are closest to each other? Which two are farthest from each other?
- Please include the apartment ids and each of the distances in miles rounded to two decimal places.

In [93]:
import pandas as pd
import numpy as np
import math, operator

#read in the .csv
aptTable = pd.DataFrame.from_csv('apartments.csv')
#create the 'locations' column


#https://gist.github.com/rochacbruno/2883505
#to find distances between (lat,long) pairs
def coordDistance(origin, destination):
    lat1, lon1 = origin
    lat2, lon2 = destination
    radius = 3956 #miles

    dlat = math.radians(lat2-lat1)
    dlon = math.radians(lon2-lon1)
    a = math.sin(dlat/2) * math.sin(dlat/2) + math.cos(math.radians(lat1)) \
        * math.cos(math.radians(lat2)) * math.sin(dlon/2) * math.sin(dlon/2)
    c = 2 * math.atan2(math.sqrt(a), math.sqrt(1-a))
    d = radius * c

    return d

def findDistances(coords, limit, op):
    aptIndex = []
    curLimit =  limit
    
    for i,c1 in enumerate(coords):
        for j,c2 in enumerate(coords[i:]):
            if i != j+i:
                distance = coordDistance(c1,c2)
                if op(distance, curLimit):
                    curLimit = distance
                    aptIndex = (i, j+i)
    return curLimit, aptIndex

def findMax(coords, indices):
    
    miles, aptIdx =   findDistances(coords, limit = -1, op = operator.gt)
    #to ensure correct index from original dataset
    idx = (indices[aptIdx[0]], indices[aptIdx[-1]])
    
    print('Maximum distances: %.2f Apartment Ids: %s')%(miles, idx)
    return miles, idx
def findMin(coords, indices):
    miles, aptIdx =  findDistances(coords, limit = np.Inf, op = operator.lt)
    #to ensure correct index from original dataset
    idx = (indices[aptIdx[0]], indices[aptIdx[-1]])
    
    print('Minimum distances: %.2f Apartment Ids: %s')%(miles, idx)
    return miles, idx

findMax(coordinates, indices = np.array(aptTable.index))
findMin(coordinates, indices = np.array(aptTable.index))


Maximum distances: 32.42 Apartment Ids: (1009, 1040)
Minimum distances: 0.06 Apartment Ids: (1003, 1024)


(0.05787223661854923, (1003, 1024))

# Problem 2
- Find the min and max rents.
- Choose a random integer in that range (inclusive), then find the number of apartments at that price or less that have Granite Countertops.

In [74]:
import random
import warnings
warnings.filterwarnings('ignore')

def findGraniteApts(data_frame = aptTable):
    r = random.randrange(min(data_frame.Price), max(data_frame.Price)+1)
    print('Returned Apts under $%d'%r)
    df = data_frame[data_frame['Price'] <= r][data_frame['Amenities'].str.contains('Granite Countertops')==True]
    print('Number of relevant apts: %d'%len(df))
    return len(df)
findGraniteApts()
          

Returned Apts under $4297
Number of relevant apts: 15


15

# Problem 3
- A friend wants an apartment with Central Air and at least three other amenities. Which apartment fulfilling these criteria has the best price per square foot and what is it, rounded to the nearest cent?

In [73]:
##assuming the 'best price' is that which is the minimum price/sqft
def bestSqFtPrice(data_frame = aptTable):
    
    centralAir = data_frame[data_frame['Amenities'].str.contains('Central Air')==True]
    centralAir['AmentityCounts'] = centralAir['Amenities'].apply(lambda a: len(a.split('|')))
    centralAir.query('AmentityCounts >= 4', inplace = True)
    centralAir['SqFtPrice'] = centralAir.Price/centralAir['Square footage']
    aptidx = centralAir['SqFtPrice'].idxmin()
    bestPrice = min(centralAir.SqFtPrice)
    assert centralAir.loc[aptidx].SqFtPrice == bestPrice
    print('Desired Apt: %d at sqftValue: %.2f $/sqft')%(aptidx, bestPrice)
    return aptidx, bestPrice

bestSqFtPrice()

Desired Apt: 1016 at sqftValue: 0.65 $/sqft


(1016, 0.65255157437567857)

# DRAFTS

Make a GET request to http://52.201.94.104:8080 with query params first_id=1001 and last_id=1050. You'll get a JSON response looking like:

In [28]:
import urllib2
import requests

In [33]:
import requests
import json

In [76]:
import requests
import json
def getMoreApts():
    #json request
    headers = {'content-type': 'application/json'}
    url = 'http://52.201.94.104:8080'
    params = {'first_id': '1001', 'last_id': '1050'}
    r = requests.post(url, params=params, headers = headers).text
    
    #to Pandas!
    p = pd.read_json(r)
    p.set_index('Id', inplace= True)
    p.Amenities = p.Amenities.apply(lambda am: str(am).strip('[]').replace("'", '|'))
    return p.to_csv('getMoreApts.csv')
    

In [81]:
aptTable = getMoreApts()  
aptTable

Amenities  Bathrooms  Bedrooms  \
Id                                                                             
1001              u|Granite Countertops|, u|Dishwasher|          1         0   
1002  u|Secure Entrance|, u|Central Air|, u|Picnic A...          1         2   
1003  u|Central Air|, u|Picnic Area|, u|Washer/Dryer...          1         1   
1004  u|Washer/Dryer|, u|Granite Countertops|, u|Fit...          1         1   
1005                              u|Off-Street Parking|          1         1   
1006  u|Secure Entrance|, u|Central Air|, u|Granite ...          1         3   
1007  u|Central Air|, u|Picnic Area|, u|Stainless St...          1         2   
1008  u|Central Air|, u|Pool|, u|Off-Street Parking|...          1         0   
1009  u|Secure Entrance|, u|Central Air|, u|Picnic A...          1         0   
1010  u|Central Air|, u|Picnic Area|, u|Stainless St...          2         3   
1011  u|Picnic Area|, u|Washer/Dryer|, u|Granite Cou...          2         3   
1012  u|Secure Entrance|, u|Off-Street Parking|, u|S...          1         0   
1013  u|Granite Countertops|, u|Stainless Steel Appl...          1         0   
1014  u|Central Air|, u|Washer/Dryer|, u|Off-Street ...          3         4   
1015                                            u|Pool|          1         3   
1016  u|Secure Entrance|, u|Central Air|, u|Off-Stre...          1         0   
1017              u|Picnic Area|, u|Utilities Included|          1         1   
1018  u|Picnic Area|, u|Pool|, u|Washer/Dryer|, u|Of...          1         1   
1019  u|Secure Entrance|, u|Picnic Area|, u|Pool|, u...          1         1   
1020             u|Central Air|, u|Pool|, u|Dishwasher|          1         2   
1021  u|Secure Entrance|, u|Washer/Dryer|, u|Granite...          2         3   
1022  u|Secure Entrance|, u|Pool|, u|Off-Street Park...          3         4   
1023                            u|Central Air|, u|Pool|          1         0   
1024      u|Pool|, u|Off-Street Parking|, u|Dishwasher|          3         3   
1025  u|Secure Entrance|, u|Granite Countertops|, u|...          2         3   
1026  u|Picnic Area|, u|Off-Street Parking|, u|Stain...          1         1   
1027  u|Picnic Area|, u|Pool|, u|Granite Countertops...          2         2   
1028  u|Pool|, u|Washer/Dryer|, u|Stainless Steel Ap...          1         0   
1029  u|Secure Entrance|, u|Central Air|, u|Fitness ...          4         4   
1030  u|Secure Entrance|, u|Central Air|, u|Picnic A...          2         4   
1031  u|Central Air|, u|Picnic Area|, u|Pool|, u|Uti...          2         4   
1032                     u|Washer/Dryer|, u|Dishwasher|          3         3   
1033  u|Granite Countertops|, u|Stainless Steel Appl...          1         2   
1034  u|Secure Entrance|, u|Granite Countertops|, u|...          2         4   
1035  u|Central Air|, u|Washer/Dryer|, u|Fitness Cen...          1         1   
1036              u|Granite Countertops|, u|Dishwasher|          1         4   
1037                        u|Secure Entrance|, u|Pool|          1         1   
1038              u|Secure Entrance|, u|Fitness Center|          2         2   
1039  u|Secure Entrance|, u|Picnic Area|, u|Washer/D...          2         3   
1040  u|Secure Entrance|, u|Central Air|, u|Washer/D...          1         2   
1041                                     u|Central Air|          2         3   
1042  u|Pool|, u|Stainless Steel Appliances|, u|Dish...          1         1   
1043  u|Picnic Area|, u|Washer/Dryer|, u|Granite Cou...          1         3   
1044  u|Pool|, u|Washer/Dryer|, u|Off-Street Parking...          2         2   
1045  u|Picnic Area|, u|Off-Street Parking|, u|Stain...          1         0   
1046  u|Central Air|, u|Picnic Area|, u|Off-Street P...          2         4   
1047             u|Washer/Dryer|, u|Off-Street Parking|          3         4   
1048                     u|Central Air|, u|Picnic Area|          1         1   
1049  u|Secure Entrance|, u|Granite Countertop

In [64]:
dist1 = np.array(f.iloc[1][['Latitude','Longitude']])
dist2 = np.array(f.iloc[4][['Latitude','Longitude']])

In [65]:
distance(dist1, dist2)

1.2035374761625464

In [93]:
locations = np.array(f.locations)
len(locations)
print (findDistances2(locations, 0))

0
At idx : 1
More than! current 5, new 100000
At idx : 2
More than! current 4, new 5
At idx : 3
More than! current 2, new 4
At idx : 4
At idx : 5
At idx : 6
At idx : 7
At idx : 8
At idx : 9
At idx : 10
More than! current 2, new 2
At idx : 11
At idx : 12
At idx : 13
At idx : 14
At idx : 15
More than! current 1, new 2
At idx : 16
At idx : 17
More than! current 1, new 1
At idx : 18
At idx : 19
At idx : 20
At idx : 21
At idx : 22
At idx : 23
More than! current 1, new 1
At idx : 24
At idx : 25
At idx : 26
At idx : 27
At idx : 28
At idx : 29
At idx : 30
At idx : 31
At idx : 32
At idx : 33
At idx : 34
More than! current 0, new 1
At idx : 35
At idx : 36
At idx : 37
At idx : 38
At idx : 39
At idx : 40
At idx : 41
At idx : 42
At idx : 43
At idx : 44
At idx : 45
At idx : 46
At idx : 47
At idx : 48
At idx : 49
At idx : 50
At idx : 51
At idx : 52
At idx : 53
At idx : 54
At idx : 55
At idx : 56
At idx : 57
At idx : 58
At idx : 59
At idx : 60
At idx : 61
At idx : 62
At idx : 63
At idx : 64
At idx : 6

RuntimeError: maximum recursion depth exceeded while calling a Python object

In [110]:
cur1 = 10000000000000
entries1 = [0,0]
for c in f.index:
    colmin, colentries = findmin(f, c)
    if c < cur1:
        cur1 = colmin
        entries1 = colentries
    

UnboundLocalError: local variable 'entries' referenced before assignment

In [105]:
print(cur1, entries1)

1000

In [65]:
f.head()

Latitude  Longitude  Bedrooms  Bathrooms  Square footage  Price  \
Id                                                                     
1   42.325319 -71.142400         2          1            1162   2722   
2   42.400188 -71.123543         0          1             260    948   
3   42.390901 -71.152410         3          3            2016   3418   
4   42.351352 -71.109718         2          1            1163   2583   
5   42.383498 -71.130352         2          2            1006   2800   

                                            Amenities       lats  \
Id                                                                 
1   Secure Entrance|Central Air|Picnic Area|Pool|W... -28.817081   
2                          Central Air|Fitness Center -28.723355   
3         Washer/Dryer|Central Air|Utilities Included -28.761509   
4   Granite Countertops|Utilities Included|Stainle... -28.758366   
5                    Granite Countertops|Washer/Dryer -28.746854   

                        ats  
Id                           
1     [42.325319, -71.1424]  
2   [42.400188, -71.123543]  
3    [42.390901, -71.15241]  
4   [42.351352, -71.109718]  
5   [42.383498, -71.130352]

In [11]:
import pandas as pd
import numpy as np
import math, operator

#read in the .csv
f = pd.DataFrame.from_csv('apartments.csv')
#create the 'locations' column
f['locations'] = f.apply(lambda x: [x['Latitude'], x['Longitude']], axis=1) 

f.head()
#get an array
locations = np.array(f.locations)
locations
len(locations)

#https://gist.github.com/rochacbruno/2883505
#to find distances between (lat,long) pairs
def distance(origin, destination):
    lat1, lon1 = origin
    lat2, lon2 = destination
    radius = 3956 #miles

    dlat = math.radians(lat2-lat1)
    dlon = math.radians(lon2-lon1)
    a = math.sin(dlat/2) * math.sin(dlat/2) + math.cos(math.radians(lat1)) \
        * math.cos(math.radians(lat2)) * math.sin(dlon/2) * math.sin(dlon/2)
    c = 2 * math.atan2(math.sqrt(a), math.sqrt(1-a))
    d = radius * c

    return d

#ERROR??? return the requested distance, and the original indices
def findDistances2(listloc, start, currentMin = 100000, currentE = [], op = operator.lt):
    e = currentE
    currentM =  currentMin
    
    if len(listloc) < 1:
        return currentM, e
    
    else:
        for i in np.arange(start+1, len(listloc)): 
            
            dist = distance(listloc[i], listloc[start])
            
            if op(dist,currentM):
                print('More than! current %f, new %f'%(dist, currentM))
                
                currentM  = abs(dist)
        
                e = (i + start, start)

        return findDistances2(listloc[1:], start = start+1, currentMin = currentM, currentE = e)

xx, yy = findDistances2(locations[:100], start = 0)
print (xx, yy)

More than! current 5.258103, new 100000.000000
More than! current 4.556834, new 5.258103
More than! current 2.452147, new 4.556834
More than! current 2.413216, new 2.452147
More than! current 1.944130, new 2.413216
More than! current 1.590034, new 1.944130
More than! current 1.302953, new 1.590034
More than! current 0.155288, new 1.302953
More than! current 0.111564, new 0.155288
More than! current 0.104741, new 0.111564
More than! current 0.084933, new 0.104741
More than! current 0.066248, new 0.084933
(0.0662483644740626, (50, 23))


In [51]:
len(locations)
def findDistances(listloc, start, currentMax = 1000000, currentE = []):
    en = currentE
    currentM =  currentMax
    
    if len(listloc) < 1:
        return currentM, en
    
    else:
        print start
        for i in np.arange(start+1, len(listloc)): 
            print ('At idx : %d' % i)
            
            dist = distance(listloc[i], listloc[start])
            
            if dist < currentM:
                print('Less than! current %d, new %d'%(dist, currentM))
                
                currentM  = abs(dist)
        
                en = (i + start, start)

        return findDistances(listloc[1:], start+1, currentMax = currentM, currentE = en)

#x, y = findDistances(locations, 0)
#print ('*****', x, y)distance(locations[1], locations[2])

def findDistances2(listloc, start, currentMin = 100000, currentE = [], op = operator.lt):
    e = currentE
    currentM =  currentMin
    
    if len(listloc) < 1:
        return currentM, e
    
    else:
        for i in np.arange(start+1, len(listloc)): 
            
            dist = distance(listloc[i], listloc[start])
            
            if op(dist,currentM):
                print('More than! current %f, new %f'%(dist, currentM))
                
                currentM  = abs(dist)
        
                e = (i + start, start)

        return findDistances2(listloc[1:], start = start+1, currentMin = currentM, currentE = e)

xx, yy = findDistances2(locations, start = 0)
print (xx, yy)

More than! current 5.258103, new 100000.000000
More than! current 4.556834, new 5.258103
More than! current 2.452147, new 4.556834
More than! current 2.413216, new 2.452147
More than! current 1.944130, new 2.413216
More than! current 1.590034, new 1.944130
More than! current 1.302953, new 1.590034
More than! current 0.155288, new 1.302953
More than! current 0.096669, new 0.155288
More than! current 0.045309, new 0.096669
More than! current 0.043805, new 0.045309
More than! current 0.030286, new 0.043805
More than! current 0.025950, new 0.030286
More than! current 0.021142, new 0.025950
More than! current 0.014042, new 0.021142
More than! current 0.005520, new 0.014042


RuntimeError: maximum recursion depth exceeded